## ELEX 4653 Quiz 2

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

#### Question 1

The `ctime(x)` function in the `time` module returns a string representation of a date and time corresponding to `x` seconds past Jan 1, 1970.  The first three characters of this string are the day of the week (e.g. "Mon" for Monday).  Write a function `day(x)` that returns the first three characters returned by `ctime(x)`. For example `day(10_000_000)` should return `'Sun'`.

#### Question 2

Write a function, `swapchar(s,p)` where `s` and `p` are strings.  The function should return a string composed of `s` with any occurence of the first character of `p` replaced by the second character of `p`.   For example `swapchar("@Here@!","@#")` would return `'#Here#!'`.

#### Question 3

Write a function `checkit(o)` that obtains `str`(ing) values from the iterable object `o` 
until a zero-length value is obtained and then returns the sum of the `len`gths of the values.
For example,
if `o` returned values from the list `['iwr', 'wu', 'amz', '', 'yzwhn']` then `checkit(o)` would return `8`.
Note that the argument `o` is not a list.

#### Question 4

Write a function `exfilter(l)` that tests successive integer-like objects in the list `l` by calling these object's `check()` method.
Your function should return a count of the values that did _not_ cause a ValueError exception.
For example, if `x.check()` raises a ValueError exception when `x` is `2` or `4` then `exfilter([1, 2, 3, 4])` would return `2`.

In [5]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.fullmatch(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.fullmatch(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    
    def Q1():
        f,a = day,randint(0,1_714_770_991)
        oa = copy.deepcopy(a)
        r = f(a)
        return r,f"{f.__name__}({oa}) returns {r}"

    def Q2():
        f = swapchar
        b = randwords(1,chars="$*_+!@",nl=(2,2))[0]
        a = b[0]*randint(0,3) + randwords(1)[0] + b[0]*randint(0,3)
        ol = copy.deepcopy((a,b))
        r = f(a,b)
        return r,f"{f.__name__}{ol} returns {r}"

    class notalist(list):
        def __init__(self,l):
            super().__init__(l)
        def __getitem__(self,i):
            raise RuntimeError("This object does not support subscripting")
    
    def Q3():
        f = checkit
        # c: two random-length lists with a null string between them
        o = randwords(randint(1,3)) + [''] + randwords(randint(1,3))
        oo = copy.deepcopy(o)
        r = checkit(notalist(o))
        return r,f"{f.__name__}({oo}) returns {r}"
        
    def Q4():
        f = exfilter
        l = list(range(1,randint(4,8)))
        random.shuffle(l)
        bad = l[::2]
        class testable(int):
            def __init__(self,x):
                super().__int__()
            def check(self):
                if self in bad:
                    raise ValueError    
        a = [testable(i) for i in l]
        oa = copy.deepcopy(a)
        r = exfilter(a)
        return r,f"{f.__name__}({oa}) returns {r}"
    
    hashvalues = '''
dPyTdPyTzQfxwd+uLZz9wBwrdPyTdPyTdPyThUgk
eK/FcNmTqARhw+5TjWoADGVHHkNgfHlktw4VtVFs
dp1q+Hd6XJAn9vMmdp1q9vMmSN5xVj+X6x5+LgOn
6x5+ZEo+ZEo+HrehZEo+ZEo+ZEo+6x5+ZEo+6x5+
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                err = f"Error during test {n}: {e}"               
        if testing:
            newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)